In [1]:
#Importa as bibliotecas necessárias
import pandas as pd
import numpy as np
from geopy.extra.rate_limiter import RateLimiter
from geopy.geocoders import Nominatim

#Importa as credencias do google drive para que a sheet possa ser acessada
from google.colab import auth
auth.authenticate_user()

import gspread
from google.auth import default
creds, _ = default()

gc = gspread.authorize(creds)

In [2]:
#Define a planilha (sheet) a ser atualizada
sheets = gc.open('taxi_zones')
#Define a aba (worksheet) a ser atualizada
sheets_page = sheets.worksheet('taxi_zones')
#Cria um dataframe com os dados já existentes da aba a ser atualizada
df_worksheet = pd.DataFrame(sheets_page.get_all_records())

#Ilustra o DataFrame
df_worksheet.head()

LocationID        Borough                     Zone service_zone
0           1            EWR           Newark Airport          EWR
1           2         Queens              Jamaica Bay    Boro Zone
2           3          Bronx  Allerton/Pelham Gardens    Boro Zone
3           4      Manhattan            Alphabet City  Yellow Zone
4           5  Staten Island            Arden Heights    Boro Zone

In [3]:
#Cria uma coluna com o endereço "completo" da zona especificada
df_worksheet['address'] = df_worksheet['Zone'] + ', New York, USA'

In [4]:
#Busca a localização de cada zona, com intervalos de 1s entre cada requisição
locator = Nominatim(user_agent='myGeocoder')
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)
df_worksheet['geoloc'] = df_worksheet['address'].apply(geocode)

#A partir do objeto criado pelo passo anterior, extraem-se a latitude e a longitude,
#criando-se uma exceção quando nao houver o objeto
df_worksheet['latitude'] = df_worksheet['geoloc'].apply(lambda loc: loc.latitude if loc else None)
df_worksheet['longitude'] = df_worksheet['geoloc'].apply(lambda loc: loc.longitude if loc else None)

#Ilustra o DataFrame resultante
df_worksheet.head()

Traceback (most recent call last):
  File "/usr/local/lib/python3.9/dist-packages/urllib3/connectionpool.py", line 449, in _make_request
    six.raise_from(e, None)
  File "<string>", line 3, in raise_from
  File "/usr/local/lib/python3.9/dist-packages/urllib3/connectionpool.py", line 444, in _make_request
    httplib_response = conn.getresponse()
  File "/usr/lib/python3.9/http/client.py", line 1377, in getresponse
    response.begin()
  File "/usr/lib/python3.9/http/client.py", line 320, in begin
    version, status, reason = self._read_status()
  File "/usr/lib/python3.9/http/client.py", line 281, in _read_status
    line = str(self.fp.readline(_MAXLINE + 1), "iso-8859-1")
  File "/usr/lib/python3.9/socket.py", line 704, in readinto
    return self._sock.recv_into(b)
  File "/usr/lib/python3.9/ssl.py", line 1242, in recv_into
    return self.read(nbytes, buffer)
  File "/usr/lib/python3.9/ssl.py", line 1100, in read
    return self._sslobj.read(len, buffer)
socket.timeout: The read 

LocationID        Borough                     Zone service_zone  \
0           1            EWR           Newark Airport          EWR   
1           2         Queens              Jamaica Bay    Boro Zone   
2           3          Bronx  Allerton/Pelham Gardens    Boro Zone   
3           4      Manhattan            Alphabet City  Yellow Zone   
4           5  Staten Island            Arden Heights    Boro Zone   

                                  address  \
0           Newark Airport, New York, USA   
1              Jamaica Bay, New York, USA   
2  Allerton/Pelham Gardens, New York, USA   
3            Alphabet City, New York, USA   
4            Arden Heights, New York, USA   

                                              geoloc   latitude  longitude  
0                                               None        NaN        NaN  
1  (Jamaica Bay, Queens County, City of New York,...  40.603994 -73.835412  
2                                               None        NaN        NaN  
3  (Alphabet City, Manhattan Community Board 3, M...  40.725102 -73.979583  
4  (Arden Heights Shopping Center, Staten Island,...  40.563700 -74.191603

In [5]:
#Separa os dados que ainda não têm latitude e longitude definidas
novo_df_worksheet = df_worksheet[df_worksheet['latitude'].isna()]

#Algum zonas inccluem dois "bairros" ao mesmo tempo. Neste ponto apenas escolhemos o primeiro bairro que aparece
novo_df_worksheet['address'] = novo_df_worksheet['Zone'].apply(lambda x: x.split('/')[0] + ', New York, USA')
novo_df_worksheet['address'] = novo_df_worksheet['Zone'].apply(lambda x: x.split('/')[0] + ', New York, USA')

#Ilustra o DataFrame resultante
novo_df_worksheet.head()

<ipython-input-5-12d856e998ab>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  novo_df_worksheet['address'] = novo_df_worksheet['Zone'].apply(lambda x: x.split('/')[0] + ', New York, USA')
<ipython-input-5-12d856e998ab>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  novo_df_worksheet['address'] = novo_df_worksheet['Zone'].apply(lambda x: x.split('/')[0] + ', New York, USA')


LocationID   Borough                     Zone service_zone  \
0            1       EWR           Newark Airport          EWR   
2            3     Bronx  Allerton/Pelham Gardens    Boro Zone   
14          15    Queens  Bay Terrace/Fort Totten    Boro Zone   
20          21  Brooklyn         Bensonhurst East    Boro Zone   
21          22  Brooklyn         Bensonhurst West    Boro Zone   

                            address geoloc  latitude  longitude  
0     Newark Airport, New York, USA   None       NaN        NaN  
2           Allerton, New York, USA   None       NaN        NaN  
14       Bay Terrace, New York, USA   None       NaN        NaN  
20  Bensonhurst East, New York, USA   None       NaN        NaN  
21  Bensonhurst West, New York, USA   None       NaN        NaN

In [6]:
#Algumas zonas são dividas em leste/oeste/norte/sul. O recurso de localização não consegue distinguir quando
#há essas variações. Uma forma de contornar isso é unificar essas zonas, removendo as palavras que definem
#a direção geográfica
novo_df_worksheet['address'] = novo_df_worksheet['address'].apply(lambda x: x.replace(' North','').replace(' South','').replace(' West','').replace(' East',''))

<ipython-input-6-d874853add2a>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  novo_df_worksheet['address'] = novo_df_worksheet['address'].apply(lambda x: x.replace(' North','').replace(' South','').replace(' West','').replace(' East',''))


In [7]:
#Busca a localização de cada zona
novo_df_worksheet['geoloc'] = novo_df_worksheet['address'].apply(geocode)

#A partir do objeto criado pelo passo anterior, extraem-se a latitude e a longitude,
#criando-se uma exceção quando nao houver o objeto
novo_df_worksheet['latitude'] = novo_df_worksheet['geoloc'].apply(lambda loc: loc.latitude if loc else None)
novo_df_worksheet['longitude'] = novo_df_worksheet['geoloc'].apply(lambda loc: loc.longitude if loc else None)

<ipython-input-7-2ab9b7465293>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  novo_df_worksheet['geoloc'] = novo_df_worksheet['address'].apply(geocode)
<ipython-input-7-2ab9b7465293>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  novo_df_worksheet['latitude'] = novo_df_worksheet['geoloc'].apply(lambda loc: loc.latitude if loc else None)
<ipython-input-7-2ab9b7465293>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = v

In [8]:
#Unifica os dados que precisaram de tratamento para se obter as localizações com os dados que 
#já tinham a latitude e longitude definidas
df_address = pd.concat([novo_df_worksheet, df_worksheet[df_worksheet['latitude'].isna() == False]])

#Classifica os dados do dataframe com base no ID da zona
df_address.sort_values(by = 'LocationID', ascending = True, inplace = True)

In [9]:
#Evidencia as zonas que ainda não possuem latitude e longitude definidas
df_address[df_address['geoloc'].isna()]

LocationID    Borough                                           Zone  \
0             1        EWR                                 Newark Airport   
102         103  Manhattan  Governor's Island/Ellis Island/Liberty Island   
103         104  Manhattan  Governor's Island/Ellis Island/Liberty Island   
104         105  Manhattan  Governor's Island/Ellis Island/Liberty Island   
178         179     Queens                                    Old Astoria   
187         188   Brooklyn                      Prospect-Lefferts Gardens   
254         255   Brooklyn                      Williamsburg (North Side)   
255         256   Brooklyn                      Williamsburg (South Side)   

    service_zone                                   address geoloc  latitude  \
0            EWR             Newark Airport, New York, USA   None       NaN   
102  Yellow Zone          Governor's Island, New York, USA   None       NaN   
103  Yellow Zone          Governor's Island, New York, USA   None       NaN   
104  Yellow Zone          Governor's Island, New York, USA   None       NaN   
178    Boro Zone                Old Astoria, New York, USA   None       NaN   
187    Boro Zone  Prospect-Lefferts Gardens, New York, USA   None       NaN   
254    Boro Zone  Williamsburg (North Side), New York, USA   None       NaN   
255    Boro Zone  Williamsburg (South Side), New York, USA   None       NaN   

     longitude  
0          NaN  
102        NaN  
103        NaN  
104        NaN  
178        NaN  
187        NaN  
254        NaN  
255        NaN

In [10]:
#Define manualmente - já que restaram pouquíssimas zonas para o ajuste - as latitude e longitude
#das zonas ainda sem estas definidas
df_address['latitude'][0] = 40.6895314
df_address['longitude'][0] = -74.17446239999998
df_address['latitude'][178] = 46.187580
df_address['longitude'][178] = -123.834114
df_address['latitude'][187] = 40.665535
df_address['longitude'][187] = -73.969749
df_address['latitude'][254] = 37.271133
df_address['longitude'][254] = -76.716614
df_address['latitude'][263] = 39.876019
df_address['longitude'][263] = -117.224121

<ipython-input-10-15f195f83e91>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_address['latitude'][0] = 40.6895314
<ipython-input-10-15f195f83e91>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_address['longitude'][0] = -74.17446239999998
<ipython-input-10-15f195f83e91>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_address['latitude'][178] = 46.187580
<ipython-input-10-15f195f83e91>:6: SettingWithCopyWarning: 
A value i

In [11]:
#Importa biblioteca necessária para o download do arquivo resultante
from google.colab import files

#Realiza o download do arquivo resultante
df_address.to_csv('taxi_zones.csv', index = False)
files.download('taxi_zones.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>